In [63]:
import sys,importlib
sys.path.append('../')
import simulation
from numpy import *
import plotly.offline as py
import plotly.graph_objs as go


In [53]:
sigma = 10
beta = 8/3
rho = 28
def lorenz(state,t):
    x,y,z = state[0],state[1],state[2]
    xdot = sigma*(y-x)
    ydot = x*(rho-z)-y
    zdot = x*y - beta*z
    return asarray((xdot,ydot,zdot))

### Coupling

In [54]:
a0,a1 = 1.5,1.2
w = 1.3

In [55]:
def coupling(stateA,stateB,t):
    x1,y1,z1 = stateA
    x2,y2,z2 = stateB
    xdot = a1*w*cos(w*t) + sigma*(y1-x1) + sigma*(x1-y1+a0+a1*sin(w*t))  -sigma*(y2-y1)
    ydot = x1*(rho-z1) - (rho-z1)*(x1+a0+a1*sin(w*t)) -(x2-x1-(a0+a1*sin(w*t)))*(rho-z1)
    zdot = x1*y1 - y1*(x1+a0+a1*sin(w*t)) -beta*(z2-z1)
    return asarray((xdot,ydot,zdot))

### Simulation

In [56]:
time = 100
delTime = .01
timeline = arange(0.0, time, delTime)

In [57]:
stateA0 = asarray([0.1,0.3,1])
stateB0 = asarray([1,3,-2])
stateA,stateB = simulation.evolveAB(lorenz,lorenz,stateA0,stateB0,couplingB=coupling,time=time,delTime=delTime)

### Synchronization - order parameter

In [64]:
py.iplot([go.Scatter(x=timeline,y=stateB[:,0]-stateA[:,0]),
         go.Scatter(x=timeline,y=stateB[:,1]-stateA[:,1]),
         go.Scatter(x=timeline,y=stateB[:,2]-stateA[:,2])])

In [69]:
def eigenvalue1(stateA,stateB,t):
    return 0*stateA[:,0]-2*sigma
def eigenvalue2(stateA,stateB,t):
    return (-1 - sqrt(-4*(a0+a1*sin(w*t))**2 - 4*stateA[:,0]*(stateA[:,0]+2*(a0+a1*sin(w*t))) + 1))
def eigenvalue3(stateA,stateB,t):
    return (-1 + sqrt(-4*(a0+a1*sin(w*t))**2 - 4*stateA[:,0]*(stateA[:,0]+2*(a0+a1*sin(w*t))) + 1))

In [70]:
py.iplot([go.Scatter(x=timeline,y=eigenvalue1(stateA,stateB,timeline)),
          go.Scatter(x=timeline,y=eigenvalue2(stateA,stateB,timeline)),
          go.Scatter(x=timeline,y=eigenvalue3(stateA,stateB,timeline))])